<a href="https://colab.research.google.com/github/Kaleab1999/text-summarization/blob/main/Text_summarization_with_BART.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install simpletransformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 250 kB 4.6 MB/s 
     |████████████████████████████████| 5.5 MB 61.7 MB/s 
     |████████████████████████████████| 43 kB 2.7 MB/s 
     |████████████████████████████████| 9.2 MB 47.7 MB/s 
     |████████████████████████████████| 1.9 MB 54.4 MB/s 
     |████████████████████████████████| 1.3 MB 60.7 MB/s 
     |████████████████████████████████| 7.6 MB 53.1 MB/s 
     |████████████████████████████████| 451 kB 76.6 MB/s 
     |████████████████████████████████| 182 kB 62.4 MB/s 
     |████████████████████████████████| 182 kB 60.3 MB/s 
     |████████████████████████████████| 168 kB 55.0 MB/s 
     |████████████████████████████████| 63 kB 2.2 MB/s 
     |████████████████████████████████| 166 kB 72.6 MB/s 
     |████████████████████████████████| 166 kB 67.8 MB/s 
     |████████████████████████████████| 162 kB 77.1 MB/s 
     |██████████████████████████████

In [ ]:
import pandas as pd

In [ ]:
df= pd.read_csv('/content/BBCarticles_csv.csv', encoding='unicode_escape')
df.head()

Summary  \
0  TimeWarner said fourth quarter sales rose 2% t...   
1  The dollar has hit its highest level against t...   
2  Yukos' owner Menatep Group says it will ask Ro...   
3  Rod Eddington, BA's chief executive, said the ...   
4  Pernod has reduced the debt it took on to fund...   

                                                Text  
0  Ad sales boost Time Warner profit\n\nQuarterly...  
1  Dollar gains on Greenspan speech\n\nThe dollar...  
2  Yukos unit buyer faces loan claim\n\nThe owner...  
3  High fuel prices hit BA's profits\n\nBritish A...  
4  Pernod takeover talk lifts Domecq\n\nShares in...

In [ ]:
df['Summary'][3]

'Rod Eddington, BA\'s chief executive, said the results were "respectable" in a third quarter when fuel costs rose by Â£106m or 47.3%.To help offset the increased price of aviation fuel, BA last year introduced a fuel surcharge for passengers.BA had previously forecast a 2% to 3% rise in full-year revenue."It is quite good on the revenue side and it shows the impact of fuel surcharges and a positive cargo development, however, operating margins down and cost impact of fuel are very strong," he said.Yet aviation analyst Mike Powell of Dresdner Kleinwort Wasserstein says BA\'s estimated annual surcharge revenues - Â£160m - will still be way short of its additional fuel costs - a predicted extra Â£250m."For the year to March 2005, the total revenue outlook is slightly better than previous guidance with a 3% to 3.5% improvement anticipated," BA chairman Martin Broughton said.Looking ahead to its full year results to March 2005, BA warned that yields - average revenues per passenger - were 

In [ ]:
from simpletransformers.seq2seq import Seq2SeqModel,Seq2SeqArgs

In [ ]:
# object creation for args same like TrainerArguments
model_args = Seq2SeqArgs() 
model_args.num_train_epochs = 5
model_args.no_save = True
model_args.evaluate_generated_text = True
model_args.evaluate_during_training = True
model_args.evaluate_during_training_verbose = True

# Initialize model
model = Seq2SeqModel(
    encoder_decoder_type="bart",
    encoder_decoder_name="facebook/bart-large",
    args=model_args,
    use_cuda=True,
)

Downloading:   0%|          | 0.00/1.63k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.02G [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/899k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/456k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

In [ ]:
df.shape

(2225, 2)

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2225 entries, 0 to 2224
Data columns (total 2 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   Summary  2225 non-null   object
 1   Text     2225 non-null   object
dtypes: object(2)
memory usage: 34.9+ KB


In [ ]:
df['target_text']= df['Summary'].astype(str) # you should change the name of columns summary as target_text and text as input_text
df['input_text']= df['Text'].astype(str)

In [ ]:
df.head()

Summary  \
0  TimeWarner said fourth quarter sales rose 2% t...   
1  The dollar has hit its highest level against t...   
2  Yukos' owner Menatep Group says it will ask Ro...   
3  Rod Eddington, BA's chief executive, said the ...   
4  Pernod has reduced the debt it took on to fund...   

                                                Text  \
0  Ad sales boost Time Warner profit\n\nQuarterly...   
1  Dollar gains on Greenspan speech\n\nThe dollar...   
2  Yukos unit buyer faces loan claim\n\nThe owner...   
3  High fuel prices hit BA's profits\n\nBritish A...   
4  Pernod takeover talk lifts Domecq\n\nShares in...   

                                         target_text  \
0  TimeWarner said fourth quarter sales rose 2% t...   
1  The dollar has hit its highest level against t...   
2  Yukos' owner Menatep Group says it will ask Ro...   
3  Rod Eddington, BA's chief executive, said the ...   
4  Pernod has reduced the debt it took on to fund...   

                                          input_text  
0  Ad sales boost Time Warner profit\n\nQuarterly...  
1  Dollar gains on Greenspan speech\n\nThe dollar...  
2  Yukos unit buyer faces loan claim\n\nThe owner...  
3  High fuel prices hit BA's profits\n\nBritish A...  
4  Pernod takeover talk lifts Domecq\n\nShares in...

In [ ]:
# split 
train_df= df.iloc[:1500, 2:]
eval_df= df.iloc[1500:,2:]

In [ ]:
train_df.shape , eval_df.shape

((1500, 2), (725, 2))

In [ ]:
def count_matches(labels, preds):
    print(labels)
    print(preds)
    return sum(
        [
            1 if label == pred else 0
            for label, pred in zip(labels, preds)
        ]
    )

In [ ]:
# Train the model
model.train_model(
    train_df, eval_data=eval_df, matches=count_matches
)

  0%|          | 0/1500 [00:00<?, ?it/s]

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

Running Epoch 0 of 5:   0%|          | 0/188 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/torch/optim/lr_scheduler.py:136: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  "https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate", UserWarning)


  0%|          | 0/725 [00:00<?, ?it/s]

...

Running Epoch 4 of 5:   0%|          | 0/188 [00:00<?, ?it/s]

  0%|          | 0/725 [00:00<?, ?it/s]

Generating outputs:   0%|          | 0/91 [00:00<?, ?it/s]

['Arsenal\'s Sol Campbell has called the rivalry between Manchester United and the Gunners "bitter and personal".I\'m starting a little with French, of course."With tensions spilling over afterwards - United boss Sir Alex Ferguson was allegedly pelted with pizza in the players\' tunnel - there is little surprise that so much is riding on the return encounter on."After all that has happened, if we beat them it will be one of our sweetest ever wins, especially because of how we lost to them up there.""Everyone at Arsenal has been waiting for this game," said Campbell."It is just more bitter and personal against United," the defender told The Guardian newspaper."We are up for this one."', 'Blackburn have said all along that they want Â£6m for the midfielder and Williams has rejected proposals from Rangers over a player-swap deal.Williams conceded any deal for Ferguson was looking "unlikely" before the close of the transfer window but Rangers still had a chance to seal the deal.Williams sa

(940,
 {'global_step': [188, 376, 564, 752, 940],
  'eval_loss': [2.012531423306727,
   1.9897186140437702,
   2.0338892124511383,
   2.0704400080900927,
   2.113172110620436],
  'train_loss': [2.0656373500823975,
   1.792868733406067,
   1.2953966856002808,
   0.8914374709129333,
   1.1915547847747803],
  'matches': [0, 0, 0, 0, 0]})

In [ ]:
# # Evaluate the model
results = model.eval_model(eval_df)

  0%|          | 0/725 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/91 [00:00<?, ?it/s]

Generating outputs:   0%|          | 0/91 [00:00<?, ?it/s]

In [ ]:
results

{'eval_loss': 2.113172110620436, 'matches': 0}

In [ ]:
# Use the model for prediction
print(
    model.predict(
        [
            """High fuel prices hit BA's profits British Airways has blamed high fuel prices for a 40% drop in profits. Reporting its results for the three months to 31 December 2004, the airline made a pre-tax profit of Â£75m ($141m) compared with Â£125m a year earlier. Rod Eddington, BA's chief executive, said the results were "respectable" in a third quarter when fuel costs rose by Â£106m or 47.3%. BA's profits were still better than market expectation of Â£59m, and it expects a rise in full-year revenues.
To help offset the increased price of aviation fuel, BA last year introduced a fuel surcharge for passengers.In October, it increased this from Â£6 to Â£10 one-way for all long-haul flights, while the short-haul surcharge was raised from Â£2.50 to Â£4 a leg. Yet aviation analyst Mike Powell of Dresdner Kleinwort Wasserstein says BA's estimated annual surcharge revenues - Â£160m - will still be way short of its additional fuel costs - a predicted extra Â£250m. Turnover for the quarter was up 4.3% to Â£1.97bn, further benefiting from a rise in cargo revenue. Looking ahead to its full year results to March 2005, BA warned that yields - average revenues per passenger - were expected to decline as it continues to lower prices in the face of competition from low-cost carriers. However, it said sales would be better than previously forecast. "For the year to March 2005, the total revenue outlook is slightly better than previous guidance with a 3% to 3.5% improvement anticipated," BA chairman Martin Broughton said. BA had previously forecast a 2% to 3% rise in full-year revenue.
It also reported on Friday that passenger numbers rose 8.1% in January. Aviation analyst Nick Van den Brul of BNP Paribas described BA's latest quarterly results as "pretty modest". "It is quite good on the revenue side and it shows the impact of fuel surcharges and a positive cargo development, however, operating margins down and cost impact of fuel are very strong," he said. Since the 11 September 2001 attacks in the United States, BA has cut 13,000 jobs as part of a major cost-cutting drive. "Our focus remains on reducing controllable costs and debt whilst continuing to invest in our products," Mr Eddington said. "For example, we have taken delivery of six Airbus A321 aircraft and next month we will start further improvements to our Club World flat beds." BA's shares closed up four pence at 274.5 pence.
            """
        ]
    )
)